In [12]:
import pandas as pd
from sklearn.model_selection import StratifiedKFold, GridSearchCV
from sklearn.model_selection import train_test_split
from sklearn.tree import DecisionTreeClassifier
import matplotlib.pyplot as plt
import numpy as np
from sklearn import tree
from sklearn.neighbors import KNeighborsClassifier
from sklearn.metrics import confusion_matrix
from sklearn.metrics import accuracy_score
from sklearn.metrics import classification_report
from sklearn.metrics import roc_curve, roc_auc_score
from sklearn.metrics import log_loss
from xgboost import XGBClassifier
from catboost import CatBoostClassifier
import pickle

In [13]:
import warnings
warnings.filterwarnings('ignore')

In [5]:
pip install xgboost

     ---------------------------------------- 89.1/89.1 MB 9.1 MB/s eta 0:00:00
Note: you may need to restart the kernel to use updated packages.


In [7]:
pip install catboost


     ---------------------------------------- 74.0/74.0 MB 9.5 MB/s eta 0:00:00
     ---------------------------------------- 47.0/47.0 kB 2.3 MB/s eta 0:00:00


In [78]:
pip install lightgbm


     ---------------------------------------- 1.0/1.0 MB 1.2 MB/s eta 0:00:00


In [39]:
binp_p = pd.read_csv("C:/Users/vishw/OneDrive/Desktop/Insurance/ML/ML_dataset.csv",index_col = 'DESYNPUF_ID')

In [13]:
#binp_pp = binp_p.sample(1500000)

In [40]:
binp_exp = pd.get_dummies(binp_p, drop_first=True)

In [41]:
X = binp_exp.drop('Inpatient_reimbursement_amount_Reimbursed', axis=1)
y = binp_exp['Inpatient_reimbursement_amount_Reimbursed']

In [42]:
X_train, X_test, y_train, y_test = train_test_split(X, y, stratify=y,
                                                    random_state=2023,
                                                    test_size=0.3)

In [43]:
gbm = XGBClassifier(random_state=2023)
params = {'learning_rate': [0.1, 0.15, 0.3, 0.35, 0.4, 0.5],
          'n_estimators': [25, 50, 75],
          'max_depth':[2, 3, 4, 5]}

In [44]:
kfold = StratifiedKFold(n_splits=5, shuffle=True, random_state=2023)


In [45]:
gcv = GridSearchCV(gbm, param_grid=params,
                   cv=kfold, scoring='roc_auc',n_jobs=-1)

In [46]:
gcv.fit(X, y)
print(gcv.best_params_)
print(gcv.best_score_)

{'learning_rate': 0.35, 'max_depth': 5, 'n_estimators': 75}
0.768464589416912


In [48]:
with open('C:/Users/vishw/OneDrive/Desktop/temp/XGboost_class', 'wb') as f:
    pickle.dump(gcv,f)

In [49]:
loaded_model = pickle.load(open('C:/Users/vishw/OneDrive/Desktop/temp/XGboost_class','rb'))

In [50]:
y_pred_prob = gcv.predict_proba(X_test)[:,1]

print(roc_auc_score(y_test, y_pred_prob))
print(log_loss(y_test, y_pred_prob))

0.7713579840684828
0.5707184155065569


In [41]:
print(roc_auc_score(y_test, y_pred_prob))

0.7729278343791174


## Naive Bayes

In [ ]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.model_selection import StratifiedKFold, cross_val_score
from sklearn.naive_bayes import BernoulliNB
from sklearn.metrics import roc_curve, roc_auc_score
from sklearn.metrics import log_loss

## First

In [47]:
kfold = StratifiedKFold(n_splits=5, shuffle=True, random_state=2023)

In [48]:
results = cross_val_score(nb, X, y, scoring='roc_auc', cv=kfold)
print(results.mean())

0.7552742662859908


## Second

In [43]:
nb = BernoulliNB()
nb.fit(X_train, y_train)

BernoulliNB()

In [44]:
y_pred_prob = nb.predict_proba(X_test)[:,1]

0.7569335756643234
0.7218847807038669


In [45]:
y_pred = nb.predict(X_test)

[[15868  7269]
 [ 6692 15171]]
0.6897555555555556


In [46]:
print(roc_auc_score(y_test, y_pred_prob))
print(log_loss(y_test, y_pred_prob))

0.7569335756643234
0.7218847807038669


## Discriminant Analysis

In [49]:
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis
from sklearn.discriminant_analysis import QuadraticDiscriminantAnalysis

## LDA

In [50]:
lda = LinearDiscriminantAnalysis()
lda.fit(X_train, y_train)

LinearDiscriminantAnalysis()

In [51]:
y_pred = lda.predict(X_test)
y_pred_prob = lda.predict_proba(X_test)[:,1]

In [52]:
print(roc_auc_score(y_test, y_pred_prob))
print(log_loss(y_test, y_pred_prob))

0.7630486646787517
0.5816619404070801


In [53]:
kfold = StratifiedKFold(n_splits=5, shuffle=True, random_state=2023)
results = cross_val_score(lda, X, y, scoring='roc_auc', cv=kfold)

In [54]:
print(results.mean())

-0.5822242869629236


## QDA

In [56]:
qda = QuadraticDiscriminantAnalysis()
qda.fit(X_train, y_train)

QuadraticDiscriminantAnalysis()

In [57]:
kfold = StratifiedKFold(n_splits=5, shuffle=True, random_state=2023)
results = cross_val_score(qda, X, y, scoring='roc_auc', cv=kfold)

In [58]:
print(results.mean())

-0.7666458875786437


## Logistic Regression

In [51]:
from sklearn.model_selection import StratifiedKFold, GridSearchCV
from sklearn.linear_model import LogisticRegression

In [52]:
kfold = StratifiedKFold(n_splits=5, shuffle=True, random_state=2023)
lr = LogisticRegression()

In [53]:
params = {'penalty':['l1','l2','elasticnet', None],
          'multi_class':['ovr', 'multinomial']}

In [54]:
gcv = GridSearchCV(lr, param_grid=params, cv=kfold, 
                   scoring='roc_auc')

In [55]:
gcv.fit(X, y)

GridSearchCV(cv=StratifiedKFold(n_splits=5, random_state=2023, shuffle=True),
             estimator=LogisticRegression(),
             param_grid={'multi_class': ['ovr', 'multinomial'],
                         'penalty': ['l1', 'l2', 'elasticnet', None]},
             scoring='roc_auc')

In [56]:
with open('C:/Users/vishw/OneDrive/Desktop/temp/LOGREG_class', 'wb') as f:
    pickle.dump(gcv,f)

In [57]:
loaded_model = pickle.load(open('C:/Users/vishw/OneDrive/Desktop/temp/LOGREG_class','rb'))

In [58]:
y_pred_prob = gcv.predict_proba(X_test)[:,1]

In [59]:
y_pred = gcv.predict(X_test)

In [60]:
print(roc_auc_score(y_test, y_pred_prob))
print(log_loss(y_test, y_pred_prob))

0.7454792262089461
0.5957708725508765


## CATBoost

In [21]:
from catboost import CatBoostClassifier

In [22]:
kfold = StratifiedKFold(n_splits=5, shuffle=True, random_state=2023)
cat_gbm =CatBoostClassifier(random_state=2023)

In [23]:
params ={'learning_rate': [0.03, 0.1],
    'depth':[4, 6, 10],
    'l2_leaf_reg': [1, 3, 5]}

In [24]:
gcv = GridSearchCV(cat_gbm, param_grid=params, cv=kfold)

gcv.fit(X, y)

0:	learn: 0.6867621	total: 200ms	remaining: 3m 19s
1:	learn: 0.6808691	total: 244ms	remaining: 2m 1s
2:	learn: 0.6752155	total: 281ms	remaining: 1m 33s
3:	learn: 0.6699680	total: 320ms	remaining: 1m 19s
4:	learn: 0.6651819	total: 357ms	remaining: 1m 11s
5:	learn: 0.6605887	total: 396ms	remaining: 1m 5s
6:	learn: 0.6562681	total: 440ms	remaining: 1m 2s
7:	learn: 0.6521019	total: 482ms	remaining: 59.8s
8:	learn: 0.6482097	total: 522ms	remaining: 57.4s
9:	learn: 0.6445836	total: 561ms	remaining: 55.6s
10:	learn: 0.6412311	total: 600ms	remaining: 53.9s
11:	learn: 0.6380214	total: 642ms	remaining: 52.8s
12:	learn: 0.6350686	total: 689ms	remaining: 52.3s
13:	learn: 0.6322593	total: 730ms	remaining: 51.4s
14:	learn: 0.6296216	total: 770ms	remaining: 50.5s
15:	learn: 0.6271046	total: 806ms	remaining: 49.6s
16:	learn: 0.6247825	total: 849ms	remaining: 49.1s
17:	learn: 0.6226046	total: 889ms	remaining: 48.5s
18:	learn: 0.6205513	total: 934ms	remaining: 48.2s
19:	learn: 0.6185869	total: 978ms	rem

163:	learn: 0.5772840	total: 6.85s	remaining: 34.9s
164:	learn: 0.5772637	total: 6.9s	remaining: 34.9s
165:	learn: 0.5772401	total: 6.95s	remaining: 34.9s
166:	learn: 0.5772165	total: 6.99s	remaining: 34.9s
167:	learn: 0.5772000	total: 7.03s	remaining: 34.8s
168:	learn: 0.5771819	total: 7.07s	remaining: 34.8s
169:	learn: 0.5771635	total: 7.11s	remaining: 34.7s
170:	learn: 0.5771443	total: 7.15s	remaining: 34.7s
171:	learn: 0.5771217	total: 7.2s	remaining: 34.6s
172:	learn: 0.5771033	total: 7.24s	remaining: 34.6s
173:	learn: 0.5770852	total: 7.28s	remaining: 34.5s
174:	learn: 0.5770653	total: 7.31s	remaining: 34.5s
175:	learn: 0.5770433	total: 7.36s	remaining: 34.4s
176:	learn: 0.5770280	total: 7.39s	remaining: 34.4s
177:	learn: 0.5770142	total: 7.43s	remaining: 34.3s
178:	learn: 0.5769955	total: 7.46s	remaining: 34.2s
179:	learn: 0.5769763	total: 7.5s	remaining: 34.2s
180:	learn: 0.5769586	total: 7.54s	remaining: 34.1s
181:	learn: 0.5769457	total: 7.58s	remaining: 34.1s
182:	learn: 0.5

326:	learn: 0.5755004	total: 13.7s	remaining: 28.2s
327:	learn: 0.5754971	total: 13.7s	remaining: 28.2s
328:	learn: 0.5754922	total: 13.8s	remaining: 28.1s
329:	learn: 0.5754860	total: 13.8s	remaining: 28.1s
330:	learn: 0.5754834	total: 13.9s	remaining: 28s
331:	learn: 0.5754759	total: 13.9s	remaining: 28s
332:	learn: 0.5754720	total: 13.9s	remaining: 27.9s
333:	learn: 0.5754693	total: 14s	remaining: 27.9s
334:	learn: 0.5754638	total: 14s	remaining: 27.9s
335:	learn: 0.5754571	total: 14.1s	remaining: 27.8s
336:	learn: 0.5754512	total: 14.1s	remaining: 27.8s
337:	learn: 0.5754399	total: 14.2s	remaining: 27.7s
338:	learn: 0.5754363	total: 14.2s	remaining: 27.7s
339:	learn: 0.5754311	total: 14.2s	remaining: 27.6s
340:	learn: 0.5754276	total: 14.3s	remaining: 27.6s
341:	learn: 0.5754238	total: 14.3s	remaining: 27.5s
342:	learn: 0.5754139	total: 14.4s	remaining: 27.5s
343:	learn: 0.5754087	total: 14.4s	remaining: 27.4s
344:	learn: 0.5754005	total: 14.4s	remaining: 27.4s
345:	learn: 0.575391

485:	learn: 0.5747143	total: 20.4s	remaining: 21.6s
486:	learn: 0.5747080	total: 20.4s	remaining: 21.5s
487:	learn: 0.5747040	total: 20.5s	remaining: 21.5s
488:	learn: 0.5747009	total: 20.5s	remaining: 21.4s
489:	learn: 0.5746963	total: 20.6s	remaining: 21.4s
490:	learn: 0.5746928	total: 20.6s	remaining: 21.3s
491:	learn: 0.5746883	total: 20.6s	remaining: 21.3s
492:	learn: 0.5746848	total: 20.7s	remaining: 21.3s
493:	learn: 0.5746817	total: 20.7s	remaining: 21.2s
494:	learn: 0.5746790	total: 20.8s	remaining: 21.2s
495:	learn: 0.5746755	total: 20.8s	remaining: 21.1s
496:	learn: 0.5746660	total: 20.8s	remaining: 21.1s
497:	learn: 0.5746629	total: 20.9s	remaining: 21.1s
498:	learn: 0.5746552	total: 20.9s	remaining: 21s
499:	learn: 0.5746525	total: 21s	remaining: 21s
500:	learn: 0.5746512	total: 21s	remaining: 20.9s
501:	learn: 0.5746479	total: 21.1s	remaining: 20.9s
502:	learn: 0.5746454	total: 21.1s	remaining: 20.9s
503:	learn: 0.5746423	total: 21.2s	remaining: 20.8s
504:	learn: 0.574638

648:	learn: 0.5741669	total: 27.5s	remaining: 14.9s
649:	learn: 0.5741613	total: 27.6s	remaining: 14.8s
650:	learn: 0.5741580	total: 27.6s	remaining: 14.8s
651:	learn: 0.5741556	total: 27.6s	remaining: 14.8s
652:	learn: 0.5741528	total: 27.7s	remaining: 14.7s
653:	learn: 0.5741498	total: 27.7s	remaining: 14.7s
654:	learn: 0.5741473	total: 27.8s	remaining: 14.6s
655:	learn: 0.5741404	total: 27.8s	remaining: 14.6s
656:	learn: 0.5741383	total: 27.9s	remaining: 14.6s
657:	learn: 0.5741361	total: 27.9s	remaining: 14.5s
658:	learn: 0.5741339	total: 28s	remaining: 14.5s
659:	learn: 0.5741314	total: 28s	remaining: 14.4s
660:	learn: 0.5741296	total: 28.1s	remaining: 14.4s
661:	learn: 0.5741264	total: 28.1s	remaining: 14.4s
662:	learn: 0.5741235	total: 28.2s	remaining: 14.3s
663:	learn: 0.5741195	total: 28.2s	remaining: 14.3s
664:	learn: 0.5741167	total: 28.3s	remaining: 14.2s
665:	learn: 0.5741132	total: 28.3s	remaining: 14.2s
666:	learn: 0.5741095	total: 28.4s	remaining: 14.2s
667:	learn: 0.57

...

390:	learn: 0.5364924	total: 1m 2s	remaining: 1m 36s
391:	learn: 0.5364384	total: 1m 2s	remaining: 1m 36s
392:	learn: 0.5363888	total: 1m 2s	remaining: 1m 36s
393:	learn: 0.5362716	total: 1m 2s	remaining: 1m 36s
394:	learn: 0.5361629	total: 1m 2s	remaining: 1m 36s
395:	learn: 0.5361184	total: 1m 2s	remaining: 1m 35s
396:	learn: 0.5360226	total: 1m 3s	remaining: 1m 35s
397:	learn: 0.5359119	total: 1m 3s	remaining: 1m 35s
398:	learn: 0.5358856	total: 1m 3s	remaining: 1m 35s
399:	learn: 0.5358294	total: 1m 3s	remaining: 1m 35s
400:	learn: 0.5357261	total: 1m 3s	remaining: 1m 35s
401:	learn: 0.5356737	total: 1m 3s	remaining: 1m 34s
402:	learn: 0.5355805	total: 1m 3s	remaining: 1m 34s
403:	learn: 0.5355480	total: 1m 4s	remaining: 1m 34s
404:	learn: 0.5355203	total: 1m 4s	remaining: 1m 34s
405:	learn: 0.5354901	total: 1m 4s	remaining: 1m 34s
406:	learn: 0.5354151	total: 1m 4s	remaining: 1m 34s
407:	learn: 0.5353777	total: 1m 4s	remaining: 1m 33s
408:	learn: 0.5353097	total: 1m 4s	remaining: 

544:	learn: 0.5263166	total: 1m 26s	remaining: 1m 12s
545:	learn: 0.5262548	total: 1m 26s	remaining: 1m 12s
546:	learn: 0.5262121	total: 1m 27s	remaining: 1m 12s
547:	learn: 0.5261098	total: 1m 27s	remaining: 1m 11s
548:	learn: 0.5260101	total: 1m 27s	remaining: 1m 11s
549:	learn: 0.5259636	total: 1m 27s	remaining: 1m 11s
550:	learn: 0.5259288	total: 1m 27s	remaining: 1m 11s
551:	learn: 0.5258463	total: 1m 27s	remaining: 1m 11s
552:	learn: 0.5257685	total: 1m 28s	remaining: 1m 11s
553:	learn: 0.5257465	total: 1m 28s	remaining: 1m 11s
554:	learn: 0.5257092	total: 1m 28s	remaining: 1m 10s
555:	learn: 0.5256955	total: 1m 28s	remaining: 1m 10s
556:	learn: 0.5256450	total: 1m 28s	remaining: 1m 10s
557:	learn: 0.5256014	total: 1m 28s	remaining: 1m 10s
558:	learn: 0.5254910	total: 1m 28s	remaining: 1m 10s
559:	learn: 0.5253948	total: 1m 29s	remaining: 1m 10s
560:	learn: 0.5253324	total: 1m 29s	remaining: 1m 9s
561:	learn: 0.5252665	total: 1m 29s	remaining: 1m 9s
562:	learn: 0.5252098	total: 1

700:	learn: 0.5183788	total: 1m 51s	remaining: 47.5s
701:	learn: 0.5183504	total: 1m 51s	remaining: 47.3s
702:	learn: 0.5183151	total: 1m 51s	remaining: 47.2s
703:	learn: 0.5182798	total: 1m 51s	remaining: 47s
704:	learn: 0.5182448	total: 1m 51s	remaining: 46.9s
705:	learn: 0.5180917	total: 1m 52s	remaining: 46.7s
706:	learn: 0.5179812	total: 1m 52s	remaining: 46.5s
707:	learn: 0.5179489	total: 1m 52s	remaining: 46.4s
708:	learn: 0.5179137	total: 1m 52s	remaining: 46.2s
709:	learn: 0.5178787	total: 1m 52s	remaining: 46.1s
710:	learn: 0.5177951	total: 1m 52s	remaining: 45.9s
711:	learn: 0.5177493	total: 1m 53s	remaining: 45.7s
712:	learn: 0.5177219	total: 1m 53s	remaining: 45.6s
713:	learn: 0.5176719	total: 1m 53s	remaining: 45.4s
714:	learn: 0.5176255	total: 1m 53s	remaining: 45.3s
715:	learn: 0.5175969	total: 1m 53s	remaining: 45.1s
716:	learn: 0.5175244	total: 1m 53s	remaining: 44.9s
717:	learn: 0.5174700	total: 1m 54s	remaining: 44.8s
718:	learn: 0.5174424	total: 1m 54s	remaining: 4

858:	learn: 0.5110784	total: 2m 16s	remaining: 22.3s
859:	learn: 0.5109587	total: 2m 16s	remaining: 22.2s
860:	learn: 0.5109238	total: 2m 16s	remaining: 22s
861:	learn: 0.5108715	total: 2m 16s	remaining: 21.9s
862:	learn: 0.5108354	total: 2m 16s	remaining: 21.7s
863:	learn: 0.5108011	total: 2m 16s	remaining: 21.5s
864:	learn: 0.5107773	total: 2m 17s	remaining: 21.4s
865:	learn: 0.5107161	total: 2m 17s	remaining: 21.2s
866:	learn: 0.5106525	total: 2m 17s	remaining: 21.1s
867:	learn: 0.5106199	total: 2m 17s	remaining: 20.9s
868:	learn: 0.5105991	total: 2m 17s	remaining: 20.8s
869:	learn: 0.5105790	total: 2m 17s	remaining: 20.6s
870:	learn: 0.5105112	total: 2m 17s	remaining: 20.4s
871:	learn: 0.5104538	total: 2m 18s	remaining: 20.3s
872:	learn: 0.5104162	total: 2m 18s	remaining: 20.1s
873:	learn: 0.5103820	total: 2m 18s	remaining: 20s
874:	learn: 0.5103320	total: 2m 18s	remaining: 19.8s
875:	learn: 0.5102427	total: 2m 18s	remaining: 19.6s
876:	learn: 0.5101938	total: 2m 18s	remaining: 19.

GridSearchCV(cv=StratifiedKFold(n_splits=5, random_state=2023, shuffle=True),
             estimator=<catboost.core.CatBoostClassifier object at 0x000001B5B5C3CE50>,
             param_grid={'depth': [4, 6, 10], 'l2_leaf_reg': [1, 3, 5],
                         'learning_rate': [0.03, 0.1]})

In [25]:
with open('C:/Users/vishw/OneDrive/Desktop/temp/catboost_class', 'wb') as f:
    pickle.dump(gcv,f)

In [26]:
loaded_model = pickle.load(open('C:/Users/vishw/OneDrive/Desktop/temp/catboost_class','rb'))

In [27]:
y_pred_prob = gcv.predict_proba(X_test)[:,1]
y_pred = gcv.predict(X_test)

In [28]:
print(roc_auc_score(y_test, y_pred_prob))

0.834287665068444
0.5059732561053326


## LightBGM

In [29]:
from lightgbm import LGBMClassifier

In [30]:
kfold = StratifiedKFold(n_splits=5, shuffle=True, random_state=2023)

lgb = LGBMClassifier(random_state=2023)

In [31]:
params = {
    'num_leaves': [7, 14, 21, 28, 31, 50],
    'learning_rate': [0.1, 0.03, 0.003],
    'max_depth': [-1, 3, 5],
    'n_estimators': [50, 100, 200, 500],
          }

In [32]:
gcv = GridSearchCV(lgb, param_grid=params, scoring='roc_auc', cv=kfold)

In [33]:
gcv.fit(X, y)

GridSearchCV(cv=StratifiedKFold(n_splits=5, random_state=2023, shuffle=True),
             estimator=LGBMClassifier(random_state=2023),
             param_grid={'learning_rate': [0.1, 0.03, 0.003],
                         'max_depth': [-1, 3, 5],
                         'n_estimators': [50, 100, 200, 500],
                         'num_leaves': [7, 14, 21, 28, 31, 50]},
             scoring='roc_auc')

In [34]:
print(gcv.best_params_)
print(gcv.best_score_)

{'learning_rate': 0.1, 'max_depth': -1, 'n_estimators': 500, 'num_leaves': 50}
0.770979516256406


In [35]:
with open('C:/Users/vishw/OneDrive/Desktop/temp/lightBGM_class', 'wb') as f:
    pickle.dump(gcv,f)

In [36]:
loaded_model = pickle.load(open('C:/Users/vishw/OneDrive/Desktop/temp/lightBGM_class','rb'))

{'learning_rate': 0.03, 'max_depth': -1, 'n_estimators': 200, 'num_leaves': 50}
0.7673743621963187


In [37]:
y_pred_prob = gcv.predict_proba(X_test)[:,1]
y_pred = gcv.predict(X_test)

In [38]:
print(roc_auc_score(y_test, y_pred_prob))
print(log_loss(y_test, y_pred_prob))

0.7873646390928709
0.5553843936635628
